In [1]:
import os
import sys
import re
import numpy as np
import pickle
from scipy.optimize import fmin
import multiprocessing as mp
import functools

In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
# statmech library setup
sys.path.append('../../statmechlib')
from statmechlib.preprocessing import Trajectory, select_nodes, scale_configuration, pair_dist_cutoff
from statmechlib.forcefields import sd2_loss, utot_EAM_per_atom, utot_EAM_per_box, ftot_EAM, udif_print, u_core
from statmechlib.preprocessing import universal_eos
from statmechlib.preprocessing import pair_dist, force_targ, get_stats_EAM_per_atom, get_stats_EAM_per_box

In [4]:
target_raw = '../data/target_raw'
target_proc = '../data/target_processed'
working = '../data/working'

In [5]:
stats_file = 'stats_marinica' # 'stats_samples'
target_file = 'target_marinica' # 'target_samples'
params_file = 'marinica_params'

In [6]:
with open(os.path.join(working, stats_file+'.pickle'), 'rb') as fi:
    stats_all = pickle.load(fi)

with open(os.path.join(working, target_file+'.pickle'), 'rb') as fi:
    targets = pickle.load(fi)

with open(os.path.join(working, params_file + '.pickle'), 'rb') as fi:
    param_list = pickle.load(fi)  

In [7]:
# select spline knots
pair_index = [1, 2, 3, 4, 5, 6, 9, 10, 11, 12, 13, 15, 16, 17, 18]
multibody_index = [0, 7, 8, 14]

p_ix = np.array([True if i in pair_index else False for i in range(len(stats_all['hyperparams']['pair']))])
m_ix = np.array([True if i in multibody_index else False for i in range(len(stats_all['hyperparams']['edens']))])

stats = select_nodes(stats_all, p_ix, m_ix)

print("pair:", np.array(stats_all['hyperparams']['pair'])[p_ix])
print("edens:", np.array(stats_all['hyperparams']['edens'])[m_ix])
print('pars', param_list[0]['hyperparams'])

('pair:', array([ 2.5648975,  2.629795 ,  2.6946925,  2.8663175,  2.973045 ,
        3.0797725,  3.5164725,  3.846445 ,  4.1764175,  4.700845 ,
        4.8953   ,  5.089755 ,  5.3429525,  5.401695 ,  5.4604375]))
('edens:', array([ 2.5,  3.1,  3.5,  4.9]))
('pars', {u'pair': [2.5648974999999998, 2.6297950000000001, 2.6946924999999999, 2.8663175000000001, 2.9730449999999999, 3.0797724999999998, 3.5164724999999999, 3.8464450000000001, 4.1764175000000003, 4.7008450000000002, 4.8952999999999998, 5.0897550000000003, 5.3429525, 5.4016950000000001, 5.4604375000000003], u'edens': [2.5, 3.1, 3.5, 4.9]})


In [8]:
multi_pars = []
for params in param_list:
    eam_params = list(params['params']['embed']) + list(params['params']['pair']) + list(params['params']['edens'])
    multi_pars.append(np.array(eam_params))

In [9]:
multi_pars

[array([ -5.94645400e+00,  -4.94770000e-02,   9.60851701e+01,
         -1.84410924e+02,   9.35784080e+01,  -7.98358265e+00,
          7.47034093e+00,  -1.52756044e+00,   1.25205933e+00,
          1.63082162e+00,  -1.41854775e+00,  -8.19936046e-01,
          1.98013514e+00,  -6.96430180e-01,   3.04546910e-02,
         -1.63131143e+00,   1.38409896e+00,  -4.20429000e-02,
          5.18217702e-01,   5.62720800e-02,   3.44164179e-02])]

In [10]:
targets['relax']['energy']

[-1139.2,
 -1127.1304857789846,
 -1136.3561067610158,
 -906.9778908696875,
 -1190.2141809371096,
 -1136.7059111110157,
 -2.9688679595213743e-239]

In [11]:
#multi_pars.append(np.array([-6.25140612e-01,  5.84924686e-05,  1.50463356e+01, -2.45628080e+00,
#        2.75467959e+00, -1.82521768e+00,  5.82623873e-01, -8.10349686e-02, 0.0]))

#for _ in range(n_walkers):
#    pars += np.random.standard_normal(multi_pars[0].shape)*0.01

In [12]:
weight_dict = {'md':1.0, 'relax':20.0, 'eos_bcc':0.0, 'eos_fcc':0.0}

for key in targets:
    targets[key]['weight'] = weight_dict[key]

In [13]:
def optimize_EAM_mp(pars, targets, stats, utot_func):
    
    output = fmin(sd2_loss, pars, args=(targets, stats, utot_EAM_per_atom, None, 0.05, 1), maxiter=100000, maxfun=100000, disp=0, full_output=1,ftol=1e-6)

    return tuple([output[1], output[0]])

In [ ]:
params_output = []

pool = mp.Pool()

for ieam in range(1):#5, len(stats_opts[it]['hyperparams'])):

    get_sd = functools.partial(sd2_loss, targets=targets, stats=stats, utot_func=utot_EAM_per_atom, ftot_func=None, dl=0.05, verbose=1)

    get_opt = functools.partial(optimize_EAM_mp, targets=targets, stats=stats, utot_func=utot_EAM_per_atom)

    # initial ordering
    print('Initial params:', multi_pars)
    
    distances = pool.map(get_sd, multi_pars)
    
    optimal_params = zip(distances, multi_pars)
    best_params = sorted(optimal_params, key=lambda param: param[0], reverse=True)
    m_pars = [p[1] for p in best_params]

    print('Best params:', best_params)
    print('ieam:', ieam)
    #m_pars = multi_pars

    for i in range(6):
        optimal_params = pool.map(get_opt, m_pars)
        best_params = sorted(optimal_params, key=lambda param: param[0], reverse=True)
        m_pars = [p[1] for p in best_params]
        
        print("Iteration {}, best params: {}".format(i, best_params))

    print('Final Best params:', best_params)
    
    params_output.append(best_params)

pool.close()
pool.join()

('Initial params:', [array([ -5.94645400e+00,  -4.94770000e-02,   9.60851701e+01,
        -1.84410924e+02,   9.35784080e+01,  -7.98358265e+00,
         7.47034093e+00,  -1.52756044e+00,   1.25205933e+00,
         1.63082162e+00,  -1.41854775e+00,  -8.19936046e-01,
         1.98013514e+00,  -6.96430180e-01,   3.04546910e-02,
        -1.63131143e+00,   1.38409896e+00,  -4.20429000e-02,
         5.18217702e-01,   5.62720800e-02,   3.44164179e-02])])
cb md 0.999966191249


//anaconda/lib/python2.7/site-packages/numpy/core/fromnumeric.py:2909: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
//anaconda/lib/python2.7/site-packages/numpy/core/_methods.py:80: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)


cb relax 0.999932598478
loss 0.00276370903806 0.00276370903806 0.0
('Best params:', [(0.00276370903805695, array([ -5.94645400e+00,  -4.94770000e-02,   9.60851701e+01,
        -1.84410924e+02,   9.35784080e+01,  -7.98358265e+00,
         7.47034093e+00,  -1.52756044e+00,   1.25205933e+00,
         1.63082162e+00,  -1.41854775e+00,  -8.19936046e-01,
         1.98013514e+00,  -6.96430180e-01,   3.04546910e-02,
        -1.63131143e+00,   1.38409896e+00,  -4.20429000e-02,
         5.18217702e-01,   5.62720800e-02,   3.44164179e-02]))])
cb md 0.999966191249


//anaconda/lib/python2.7/site-packages/numpy/core/fromnumeric.py:2909: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
//anaconda/lib/python2.7/site-packages/numpy/core/_methods.py:80: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)


cb relax 0.999932598478
loss 0.00276370903806 0.00276370903806 0.0
cb md 0.999938006723
cb relax 0.99318407124
loss 0.27307141498 0.27307141498 0.0
cb md 0.999962927417
cb relax 0.999915690856
loss 0.00344655877003 0.00344655877003 0.0
cb md 0.999963151405
cb relax 0.999933769876
loss 0.0027229318319 0.0027229318319 0.0
cb md 0.999977020332
cb relax 0.999923164663
loss 0.00311941233689 0.00311941233689 0.0
cb md 0.999953032373
cb relax 0.999934804609
loss 0.00270177997597 0.00270177997597 0.0
cb md 0.999969727
cb relax 0.999933693947
loss 0.00271281773191 0.00271281773191 0.0
cb md 0.999960798555
cb relax 0.999894208528
loss 0.00431013688807 0.00431013688807 0.0
cb md 0.999967411526
cb relax 0.999941336036
loss 0.00241175879221 0.00241175879221 0.0
cb md 0.999969511032
cb relax 0.99945856762
loss 0.0217202280597 0.0217202280597 0.0
cb md 0.999984465955
cb relax 0.99181882639
loss 0.327725199291 0.327725199291 0.0
cb md 0.999870645938
cb relax 0.983481942569
loss 0.662808040775 0.662808

...

cb relax 0.999999998129
loss 2.09860694959e-06 2.09860694959e-06 0.0
cb md 0.99999898805
cb relax 0.999999998134
loss 2.09854331765e-06 2.09854331765e-06 0.0
cb md 0.999998988556
cb relax 0.99999999811
loss 2.0984919413e-06 2.0984919413e-06 0.0
cb md 0.999998987778
cb relax 0.999999998148
loss 2.09854433325e-06 2.09854433325e-06 0.0
cb md 0.999998987729
cb relax 0.999999998151
loss 2.09852162655e-06 2.09852162655e-06 0.0
cb md 0.999998987856
cb relax 0.999999998142
loss 2.0985931568e-06 2.0985931568e-06 0.0
cb md 0.999998987447
cb relax 0.999999998163
loss 2.0985936287e-06 2.0985936287e-06 0.0
cb md 0.999998987499
cb relax 0.999999998162
loss 2.09851144352e-06 2.09851144352e-06 0.0
cb md 0.999998987739
cb relax 0.999999998151
loss 2.09849324991e-06 2.09849324991e-06 0.0
cb md 0.99999898844
cb relax 0.999999998114
loss 2.09855093574e-06 2.09855093574e-06 0.0
cb md 0.999998987693
cb relax 0.999999998152
loss 2.09853845623e-06 2.09853845623e-06 0.0
cb md 0.999998987538
cb relax 0.99999999

loss 2.09764501892e-06 2.09764501892e-06 0.0
cb md 0.999998987559
cb relax 0.99999999818
loss 2.09766968659e-06 2.09766968659e-06 0.0
cb md nan
cb relax 0.999999998174
loss nan nan 0.0
cb md 0.999998988423
cb relax 0.999999998133
loss 2.09781495892e-06 2.09781495892e-06 0.0
cb md 0.999998988404
cb relax 0.99999999814
loss 2.0976033764e-06 2.0976033764e-06 0.0
cb md nan
cb relax 0.999999998132
loss nan nan 0.0
cb md 0.999998988407
cb relax 0.99999999814
loss 2.09758518784e-06 2.09758518784e-06 0.0
cb md nan
cb relax 0.999999998133
loss nan nan 0.0
cb md 0.999998987979
cb relax 0.999999998161
loss 2.09759337513e-06 2.09759337513e-06 0.0
cb md 0.999998987004
cb relax 0.999999998207
loss 2.097702008e-06 2.097702008e-06 0.0
cb md 0.999998987071
cb relax 0.999999998207
loss 2.0975909015e-06 2.0975909015e-06 0.0
cb md 0.999998987352
cb relax 0.999999998193
loss 2.09758481618e-06 2.09758481618e-06 0.0
cb md 0.999998986667
cb relax 0.999999998224
loss 2.09768845529e-06 2.09768845529e-06 0.0
cb 

cb md 0.99999898616
cb relax 0.999999998265
loss 2.09706096846e-06 2.09706096846e-06 0.0
cb md 0.999998986501
cb relax 0.99999999825
loss 2.09699275568e-06 2.09699275568e-06 0.0
cb md 0.999998986609
cb relax 0.999999998247
loss 2.09689505043e-06 2.09689505043e-06 0.0
cb md 0.999998986077
cb relax 0.999999998271
loss 2.09700195839e-06 2.09700195839e-06 0.0
cb md 0.999998986702
cb relax 0.999999998244
loss 2.09684978924e-06 2.09684978924e-06 0.0
cb md 0.999998987377
cb relax 0.99999999821
loss 2.09684631512e-06 2.09684631512e-06 0.0
cb md 0.999998987194
cb relax 0.999999998219
loss 2.09685773256e-06 2.09685773256e-06 0.0
cb md 0.999998985973
cb relax 0.99999999828
loss 2.09683418932e-06 2.09683418932e-06 0.0
cb md 0.999998985769
cb relax 0.999999998289
loss 2.09688558257e-06 2.09688558257e-06 0.0
cb md 0.999998987444
cb relax 0.999999998202
loss 2.09703369785e-06 2.09703369785e-06 0.0
cb md 0.999998985578
cb relax 0.999999998301
loss 2.09678733285e-06 2.09678733285e-06 0.0
cb md 0.999998

cb md 0.999998988042
cb relax 0.999999998197
loss 2.0960392718e-06 2.0960392718e-06 0.0
cb md 0.999998985897
cb relax 0.999999998303
loss 2.0960758522e-06 2.0960758522e-06 0.0
cb md 0.999998986032
cb relax 0.999999998302
loss 2.09583899025e-06 2.09583899025e-06 0.0
cb md 0.999998987372
cb relax 0.999999998238
loss 2.09573443809e-06 2.09573443809e-06 0.0
cb md 0.999998987907
cb relax 0.999999998215
loss 2.09557174209e-06 2.09557174209e-06 0.0
cb md 0.999998986099
cb relax 0.999999998303
loss 2.09569249561e-06 2.09569249561e-06 0.0
cb md 0.999998987025
cb relax 0.999999998255
loss 2.09574447163e-06 2.09574447163e-06 0.0
cb md 0.999998986261
cb relax 0.999999998296
loss 2.09562410554e-06 2.09562410554e-06 0.0
cb md 0.999998986774
cb relax 0.999999998267
loss 2.09577318772e-06 2.09577318772e-06 0.0
cb md 0.99999898719
cb relax 0.999999998246
loss 2.09576706878e-06 2.09576706878e-06 0.0
cb md 0.999998987441
cb relax 0.999999998232
loss 2.0958430949e-06 2.0958430949e-06 0.0
cb md 0.999998987

cb relax 0.999999998574
loss 2.0929774746e-06 2.0929774746e-06 0.0
cb md nan
cb relax 0.999999998631
loss nan nan 0.0
cb md 0.999998981153
cb relax 0.999999998605
loss 2.09350154687e-06 2.09350154687e-06 0.0
cb md 0.999998981343
cb relax 0.999999998601
loss 2.09325726237e-06 2.09325726237e-06 0.0
cb md 0.999998983845
cb relax 0.99999999848
loss 2.09311285752e-06 2.09311285752e-06 0.0
cb md 0.999998982367
cb relax 0.99999999856
loss 2.0928502961e-06 2.0928502961e-06 0.0
cb md 0.999998981885
cb relax 0.999999998591
loss 2.09259580023e-06 2.09259580023e-06 0.0
cb md 0.999998983219
cb relax 0.999999998518
loss 2.09283179388e-06 2.09283179388e-06 0.0
cb md 0.999998983923
cb relax 0.99999999848
loss 2.09295364704e-06 2.09295364704e-06 0.0
cb md 0.999998983688
cb relax 0.999999998497
loss 2.09274779298e-06 2.09274779298e-06 0.0
cb md 0.999998980447
cb relax 0.999999998647
loss 2.09322395251e-06 2.09322395251e-06 0.0
cb md 0.999998980139
cb relax 0.99999999867
loss 2.09292883612e-06 2.09292883

In [ ]:
# store hyperparameters and output parameters in a single file

params_optimal = []
for pars in params_output:
    n_pair = len(stats['hyperparams']['pair'])
    n_edens = len(stats['hyperparams']['edens'])
    params_dict = {'embed':list(pars[0:2]),
                   'pair':list(pars[2:2+n_pair]),
                   'edens':list(pars[2+n_pair:])}

    params_optimal.append({'hyperparams':stats['hyperparams'],'params':params_dict})

try:
    with open(os.path.join(working, 'params_store'+'.pickle'), 'rb') as fi:
        params_store = pickle.load(fi)    
except IOError:
    print('no file')
    params_store = []
    
params_store.extend(params_optimal)

with open(os.path.join(working, "params_store.pickle"), 'wb') as fo:
    pickle.dump(params_store, fo, protocol=2)